# **Laboratory 3** : visualization with igraph

## References

https://networkx.org/

https://igraph.org/python/doc/igraph

https://igraph.org/python/doc/tutorial/tutorial.html

https://pyvis.readthedocs.io/en/latest/

## Setup

In [ ]:
import pandas as pd
import networkx as nx
import igraph as ig
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors

## Importing the data and creating a networkx graph

In [ ]:
# Step 1: Import CSV files into pandas DataFrames
edges_df = pd.read_csv("friendship_network_edges.csv", delimiter=",", dtype={"Weight": int})
nodes_df = pd.read_csv("friendship_network_nodes.csv", delimiter=";")

# Step 2: Create a NetworkX graph from the data
G_nx = nx.Graph()

# Add nodes with attributes
for _, row in nodes_df.iterrows():
    G_nx.add_node(row["Id"], gender=row["Gender"])

# Add edges with weights
for _, row in edges_df.iterrows():
    G_nx.add_edge(row["Source"], row["Target"], weight=row["Weight"])


## Converting to igraph and calculating network properties

In [ ]:
# Step 3: Convert NetworkX graph to iGraph
G_ig = ig.Graph.from_networkx(G_nx)
# Step 4: Calculate metrics in iGraph
G_ig.vs["degree"] = G_ig.degree()
G_ig.vs["pagerank"] = G_ig.pagerank()
G_ig.vs["modularity_class"] = G_ig.community_multilevel(weights="weight").membership

In [ ]:
# Loop through each node (vertex) in the graph
for vertex in G_ig.vs:
    print(f"Node: {vertex['_nx_name']}")
    print(f"Degree: {vertex['degree']}")
    print(f"Gender: {vertex['gender']}")
    print(f"PageRank: {vertex['pagerank']}")
    print(f"Modularity Class: {vertex['modularity_class']}")
    print("-" * 50)


In [ ]:
# Loop through each edge in the graph
for edge in G_ig.es:
    source = edge.source  # Source node of the edge
    target = edge.target  # Target node of the edge
    weight = edge['weight']  # Weight attribute of the edge
    print(f"Edge: {G_ig.vs[source]['_nx_name']} -> {G_ig.vs[target]['_nx_name']}")
    print(f"Weight: {weight}")
    print("-" * 50)

## Visualizing the graph

In [ ]:
ig.plot(G_ig)

### Node size by degree

In [ ]:
# Plot Step 1 Node size by degree
node_sizes = [4 * deg for deg in G_ig.vs["degree"]]  # Scale node size by degree

fig, ax = plt.subplots(figsize=(10, 10))  # Ensure the figure is set

ig.plot(
    G_ig,
    vertex_size=node_sizes,
    vertex_label = G_ig.vs["_nx_name"],
    target=ax,  # Plot directly into the axes
    margin=50
)

plt.title("Step 1: Node Size by Degree")
plt.show()


### Node color by property (gender)

In [ ]:
# Plot Step 2: Add node color by gender
gender_color_map = {"Female": "purple", "Male": "green"}
node_colors = [gender_color_map[gender] for gender in G_ig.vs["gender"]]

fig, ax = plt.subplots(figsize=(10, 10))  # Ensure the figure is set

# Plot the graph
ig.plot(
    G_ig,
    vertex_size=node_sizes,
    vertex_color=node_colors,
    vertex_label=G_ig.vs["_nx_name"],
    target=ax,
    margin=50
)

plt.title("Step 2: Node Color by Gender")
plt.show()


### Edge thickness by weight

In [ ]:
# Plot Step 2: Add node color by gender
edge_weights = [int(weight/3) for weight in G_ig.es["weight"]]

fig, ax = plt.subplots(figsize=(10, 10))

# Plot the graph
ig.plot(
    G_ig,
    vertex_size=node_sizes,
    vertex_color=node_colors,
    vertex_label=G_ig.vs["_nx_name"],
    edge_width=edge_weights,
    target=ax,
    margin=50
)

plt.title("Step 3: Edge Width by Weight")
plt.show()


### Applying a force-based layout algorithm

In [ ]:
# Apply force-based layout (Fruchterman-Reingold)
layout_fr = G_ig.layout_fruchterman_reingold()

# Step 4: Force-Based Layout
fig, ax = plt.subplots(figsize=(10, 10))

ig.plot(
    G_ig,
    vertex_size=node_sizes,
    vertex_color=node_colors,
    vertex_label=G_ig.vs["_nx_name"],
    edge_width=edge_weights,
    layout=layout_fr,
    target=ax,
    margin=50
)

plt.title("Step 4: Force-Based Layout")
plt.show()


### Node size by pagerank, node color by modularity

In [ ]:
# Step 5: Resize nodes by PageRank and recolor by modularity
node_sizes_pagerank = [1000 * pr for pr in G_ig.vs["pagerank"]]
community_colors = list(mcolors.TABLEAU_COLORS.values())
node_colors_community = [
    community_colors[mod % len(community_colors)] for mod in G_ig.vs["modularity_class"]
]

fig, ax = plt.subplots(figsize=(10, 10))

ig.plot(
    G_ig,
    vertex_size=node_sizes_pagerank,
    vertex_color=node_colors_community,
    vertex_label=G_ig.vs["_nx_name"],
    edge_width=edge_weights,
    layout=layout_fr,
    target=ax,
    margin=50
)

plt.title("Step 5: Node Size by PageRank, Color by Community")
plt.show()

## Interactive visualization

In [ ]:
!pip install pyvis

In [ ]:
# Convert iGraph to NetworkX
G_nx = nx.Graph()

# Convert the nodes
for v in G_ig.vs:
    node_attrs = {key: v[key] for key in v.attributes()}  # Extract node attributes
    G_nx.add_node(v['_nx_name'], **node_attrs)  # Add node with attributes

# Convert the edges
for e in G_ig.es:
    G_nx.add_edge(G_ig.vs[e.source]['_nx_name'], G_ig.vs[e.target]['_nx_name'], weight=e['weight'])

# Check the resulting NetworkX graph
print("Nodes in NetworkX graph:", G_nx.nodes(data=True))
print("Edges in NetworkX graph:", G_nx.edges(data=True))

In [ ]:
from pyvis.network import Network
from IPython.display import display, HTML


# Create a pyvis network object
net = Network(notebook=True, cdn_resources='in_line')

# Add NetworkX graph to pyvis
net.from_nx(G_nx)

# Show the network in an HTML file
net.show("network.html")


In [ ]:
display(HTML('network.html'))


In [ ]:
from pyvis.network import Network
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np

# Assuming G is your NetworkX graph

G = G_nx
# Create a PyVis network object
net = Network(notebook=True, cdn_resources='in_line')

# Define colors based on modularity classes
modularity_classes = list(set(nx.get_node_attributes(G, 'modularity_class').values()))
mod_colors = plt.cm.viridis(np.linspace(0, 1, len(modularity_classes)))

# Map modularity class to a color
modularity_color_map = {mod_class: mod_colors[i] for i, mod_class in enumerate(modularity_classes)}

# Add nodes to PyVis network
for node in G.nodes:
    mod_class = G.nodes[node]['modularity_class']
    pagerank = G.nodes[node].get('pagerank', 0)  # Default to 0 if no pagerank attribute
    size = 20 + 500 * pagerank  # Scaling size based on PageRank
    color = modularity_color_map.get(mod_class, 'gray')  # Default to gray if no modularity class
    label = G.nodes[node].get('_nx_name', node)  # Default to node name if no _nx_name attribute

    # Ensure color is in RGB format or hex string
    if isinstance(color, np.ndarray):  # If color is an ndarray, convert to hex
        color = '#{:02x}{:02x}{:02x}'.format(int(color[0]*255), int(color[1]*255), int(color[2]*255))

    # Add node to PyVis network with size and color
    net.add_node(node, label=label, size=int(size), color=color)

# Add edges to PyVis network
for u, v in G.edges:
    net.add_edge(u, v)

# Show the network
net.show("network_graph.html")


In [ ]:
display(HTML('network_graph.html'))
